In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

In [2]:
from datasets import load_dataset

dataset = load_dataset("tner/bc5cdr")

bc5cdr/train/0000.parquet:   0%|          | 0.00/367k [00:00<?, ?B/s]

bc5cdr/validation/0000.parquet:   0%|          | 0.00/364k [00:00<?, ?B/s]

bc5cdr/test/0000.parquet:   0%|          | 0.00/386k [00:00<?, ?B/s]

Generating train split:   0%|          | 0/5228 [00:00<?, ? examples/s]

Generating validation split:   0%|          | 0/5330 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/5865 [00:00<?, ? examples/s]

In [ ]:
def filter_for_drugs(example):

{        """Keep only chemical/drug annotations"""

        filtered_tags = []
        filtered_tokens = []


        current_tag = []
        current_tokens = []

        # Assuming labels are integers: 0 for 'O', 1 for 'B-Chemical', 2 for 'I-Chemical'
        label_mapping = {0: 'O', 1: 'B-Chemical', 2: 'I-Chemical'}


        for token, tag in zip(example['tokens'], example['tags']):
            # Convert tag to string using the label mapping
            tag_str = label_mapping.get(tag, 'O')  # Default to 'O' if tag not found in mapping

            # BC5CDR uses BIO tagging for chemicals
            if tag_str.startswith('B-Chemical') or tag_str.startswith('I-Chemical'):
                current_tag.append(tag_str)  # Append the string representation
                current_tokens.append(token)
            elif tag_str == 'O' and len(current_tag) > 0:
                filtered_tags.extend(current_tag)
                filtered_tokens.extend(current_tokens)
                filtered_tags.append(tag_str)  # Append the string representation
                filtered_tokens.append(token)
                current_tag = []
                current_tokens = []
            elif tag_str == 'O':
                filtered_tags.append(tag_str)  # Append the string representation
                filtered_tokens.append(token)
        return {
            'tokens': filtered_tokens,
            'tags': filtered_tags
        }
        }

In [5]:
 filtered_dataset = dataset.map(filter_for_drugs, remove_columns=dataset['train'].column_names)
    

Map:   0%|          | 0/5228 [00:00<?, ? examples/s]

Map:   0%|          | 0/5330 [00:00<?, ? examples/s]

Map:   0%|          | 0/5865 [00:00<?, ? examples/s]

In [6]:
filtered_dataset

DatasetDict({
    train: Dataset({
        features: ['tokens', 'tags'],
        num_rows: 5228
    })
    validation: Dataset({
        features: ['tokens', 'tags'],
        num_rows: 5330
    })
    test: Dataset({
        features: ['tokens', 'tags'],
        num_rows: 5865
    })
})

In [9]:
filtered_dataset['train'].to_pandas()

tokens  \
0     [Naloxone, reverses, the, antihypertensive, ef...   
1     [In, unanesthetized, ,, spontaneously, hyperte...   
2                              [2, to, 2, mg, /, kg, .]   
3     [The, hypotensive, effect, of, 100, mg, /, kg,...   
4     [Naloxone, alone, did, not, affect, either, bl...   
...                                                 ...   
5223  [In, mice, ,, apomorphine, produced, qualitati...   
5224  [Drug, -, induced, gross, activity, counts, we...   
5225  [By, contrast, ,, apomorphine, -, induced, loc...   
5226  [Dopamine, turnover, ratios, (, DOPAC, :, DA, ...   
5227  [However, ,, apomorphine, -, induced, reductio...   

                                                   tags  
0            [B-Chemical, O, O, O, O, O, B-Chemical, O]  
1     [O, O, O, O, I-Chemical, O, O, O, O, O, O, O, ...  
2                                 [O, O, O, O, O, O, O]  
3     [O, I-Chemical, O, O, O, O, O, O, B-Chemical, ...  
4         [B-Chemical, O, O, O, O, O, O, O, O, O, O, O]  
...                                                 ...  
5223  [O, O, O, B-Chemical, O, O, O, O, O, O, O, O, ...  
5224  [O, O, O, O, O, O, O, O, O, O, O, O, O, O, O, ...  
5225  [O, O, O, B-Chemical, O, O, O, O, O, O, O, O, ...  
5226  [B-Chemical, O, O, O, B-Chemical, O, B-Chemica...  
5227                  [O, O, B-Chemical, O, O, O, O, O]  

[5228 rows x 2 columns]

In [ ]:
def preprocess_for_drug_ner(dataset, tokenizer, max_length=128):
    """
    Preprocess the dataset for drug NER task
    """

    # Define label mapping for chemical/drug entities
    label2id = {
        'O': 0,          # Outside the entity
        'B-Chemical': 1, # Beginning of a chemical entity
        'I-Chemical': 2  # Inside a chemical entity
    }
    id2label = {v: k for k, v in label2id.items()}

    def tokenize_and_align_labels(examples):
        # Tokenize the inputs and align the labels
        tokenized_inputs = tokenizer(
            examples["tokens"],        # Tokenized input sentences
            truncation=True,            # Truncate to the max_length
            is_split_into_words=True,   # Specify that the input is split into words
            padding="max_length",       # Pad to the max_length
            max_length=max_length      # Maximum token length
        )

        labels = []
      
        for i, label in enumerate(examples["tags"]):
            word_ids = tokenized_inputs.word_ids(batch_index=i)
      
            
            previous_word_idx = None
            label_ids = []

            # Loop through each token's word index
            for word_idx in word_ids:
            
                
                if word_idx is None:
                    label_ids.append(-100)  # Special token (e.g., padding) - ignore in loss calculation
                elif word_idx != previous_word_idx:
                    label_ids.append(label2id[label[word_idx]])  # Add the label for the current word
                else:
                    # For tokens that are part of the same word, use -100 to avoid counting them multiple times
                    label_ids.append(-100)

                previous_word_idx = word_idx

            labels.append(label_ids)

        # Add the labels to the tokenized inputs
        
        
        tokenized_inputs["labels"] = labels
        return tokenized_inputs

    # Process the dataset using the tokenization and label alignment function
    tokenized_dataset = dataset.map(
        tokenize_and_align_labels,  # Function to apply
        batched=True,                # Apply in batches
        remove_columns=dataset['train'].column_names  # Remove original columns after processing
    )

    return tokenized_dataset, label2id, id2label


In [ ]:
from transformers import AutoTokenizer, AutoModelForTokenClassification, TrainingArguments, Trainer
model_name = "dmis-lab/biobert-v1.1"
tokenizer = AutoTokenizer.from_pretrained(model_name)


The cache for model files in Transformers v4.22.0 has been updated. Migrating your old cache. This is a one-time only operation. You can interrupt this and resume the migration later on by calling `transformers.utils.move_cache()`.


0it [00:00, ?it/s]

tokenizer_config.json:   0%|          | 0.00/49.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/462 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/213k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

In [14]:
processed_dataset, label2id, id2label = preprocess_for_drug_ner(filtered_dataset, tokenizer)


Map:   0%|          | 0/5228 [00:00<?, ? examples/s]

Map:   0%|          | 0/5330 [00:00<?, ? examples/s]

Map:   0%|          | 0/5865 [00:00<?, ? examples/s]

In [15]:
  model = AutoModelForTokenClassification.from_pretrained(

        model_name,

        num_labels=len(label2id),

        id2label=id2label,

        label2id=label2id

    )

pytorch_model.bin:   0%|          | 0.00/433M [00:00<?, ?B/s]

Some weights of BertForTokenClassification were not initialized from the model checkpoint at dmis-lab/biobert-v1.1 and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [16]:
 training_args = TrainingArguments(

        output_dir="./drug-ner-results",

        evaluation_strategy="epoch",

        learning_rate=2e-5,

        per_device_train_batch_size=16,

        per_device_eval_batch_size=16,

        num_train_epochs=3,

        weight_decay=0.01,

        logging_dir="./logs",

    )


/opt/conda/lib/python3.10/site-packages/transformers/training_args.py:1545: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(


In [ ]:

trainer = Trainer(

        model=model,

        args=training_args,

        train_dataset=processed_dataset["train"],

        eval_dataset=processed_dataset["validation"],

    )


In [ ]:
trainer.train()

wandb: WARNING The `run_name` is currently set to the same value as `TrainingArguments.output_dir`. If this was not intended, please specify a different run name by setting the `TrainingArguments.run_name` parameter.
wandb: Using wandb-core as the SDK backend. Please refer to https://wandb.me/wandb-core for more information.
wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter, or press ctrl+c to quit:

  ········


wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


TrainOutput(global_step=981, training_loss=0.042699783220203645, metrics={'train_runtime': 284.7641, 'train_samples_per_second': 55.077, 'train_steps_per_second': 3.445, 'total_flos': 1024553846006784.0, 'train_loss': 0.042699783220203645, 'epoch': 3.0})

In [21]:
from transformers import pipeline
import torch

# Check if a GPU is available
device = 0 if torch.cuda.is_available() else -1

# Initialize the pipeline with the device argument
ner_pipeline = pipeline("ner", model=model, tokenizer=tokenizer, aggregation_strategy="simple", device=device)


In [22]:
file_path = "/kaggle/input/for-nlp/1-s2.0-S0273230024000540-mmc1.xlsx"
df = pd.read_excel(file_path)


In [23]:
text_column = "Answer"

In [ ]:
df["Entities"] = df[text_column].apply(lambda x: ner_pipeline(x) if pd.notnull(x) else [])

You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset


In [ ]:
output_file_path = "/kaggle/working/output_file.xlsx"
df.to_excel(output_file_path, index=False)

In [26]:
print("NER results have been saved to:", output_file_path)


NER results have been saved to: /kaggle/working/output_file.xlsx


In [29]:
answer = pd.read_excel("/kaggle/working/output_file.xlsx")

In [31]:
answer['Entities']

0       [{'entity_group': 'Chemical', 'score': 0.66055...
1       [{'entity_group': 'Chemical', 'score': 0.99845...
2                                                      []
3       [{'entity_group': 'Chemical', 'score': 0.99917...
4       [{'entity_group': 'Chemical', 'score': 0.99881...
                              ...                        
1760    [{'entity_group': 'Chemical', 'score': 0.99846...
1761    [{'entity_group': 'Chemical', 'score': 0.78615...
1762    [{'entity_group': 'Chemical', 'score': 0.99784...
1763    [{'entity_group': 'Chemical', 'score': 0.99835...
1764    [{'entity_group': 'Chemical', 'score': 0.62831...
Name: Entities, Length: 1765, dtype: object

In [ ]:
pd.set_option("display.max_colwidth", None)  # Show full content of each cell
pd.set_option("display.max_rows", None)      # Display all rows

# Display the DataFrame
print(df["Entities"])


0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       